In [ ]:
#PS: PRECISA salvar a api no seu docs pessoal antes de rodar, mas uma vez que ele salva não precisa salvar mais
from google.colab import drive
import os
import json
import requests as rq

drive.mount('/content/drive', force_remount=True)

def SalvarApi(url, nome_arquivo):
    pasta = "/content/drive/MyDrive/Dataset"
    os.makedirs(pasta, exist_ok=True)
    caminho_arquivo = os.path.join(pasta, nome_arquivo)

    response = rq.get(url)
    if response.status_code == 200:
        data = response.json()
        with open(caminho_arquivo, 'w') as f:
            json.dump(data, f, indent=4)
        print(f"Dados salvos em {caminho_arquivo}")
    else:
        print(f"Erro ({response.status_code}) ao acessar {url}")

SalvarApi("https://ps99.biggamesapi.io/api/exists", "pets_data.json")
SalvarApi("https://ps99.biggamesapi.io/api/rap", "rap_data.json")


Mounted at /content/drive
Dados salvos em /content/drive/MyDrive/Dataset/pets_data.json
Dados salvos em /content/drive/MyDrive/Dataset/rap_data.json


In [ ]:
#Carregando os arquivos necessários
#Se já tiver a Api salva é só clicar aqui e em "Ambiente de Execução > Executar Célula e Abaixo"
import json
import pandas as pd
import numpy as np
from google.colab import drive,files
drive.mount('/content/drive', force_remount=True)


path = "/content/drive/MyDrive/Dataset"

arquivos = ["pets_data.json", "rap_data.json"]
dfs_iniciais = []
for arquivo in arquivos:
  caminho = f"{path}/{arquivo}"
  with open(caminho, 'r', encoding='utf-8') as f:
    data = json.load(f)
    data = data.get("data", data)
    df_criada = pd.DataFrame(data)
    dfs_iniciais.append(df_criada)

#Montando os dfs
#É normal demorar um pouco para carregar a tabela
pd.set_option("display.max_rows", None)
pd.set_option('display.float_format', '{:,.0f}'.format)

df_relev1 = dfs_iniciais[0].loc[dfs_iniciais[0]["category"] == "Pet"].copy()
df_relev2 = dfs_iniciais[1].loc[dfs_iniciais[1]["category"] == "Pet"].copy()
df_relev2.reset_index(drop=True, inplace=True)

df_relev1["Id"] = df_relev1["configData"].apply(lambda x: x.get("id", "Desconhecido"))
df_relev1["Raridade"] = df_relev1["configData"].apply(lambda x: str(x.get("pt", "0")))
df_relev1["Shiny"] = df_relev1["configData"].apply(lambda x: bool(x.get("sh", False)))
df_relev1.rename(columns={"value": "Existe"}, inplace=True)

df_relev2["Id"] = df_relev2["configData"].apply(lambda x: x.get("id", "Desconhecido"))
df_relev2["Raridade"] = df_relev2["configData"].apply(lambda x: str(x.get("pt", "0")))
df_relev2["Shiny"] = df_relev2["configData"].apply(lambda x: bool(x.get("sh", False)))
df_relev2.rename(columns={"value": "Valor"}, inplace=True)

raridade_nome = {
    "0": "Normal",
    "1": "Golden",
    "2": "Rainbow"
}

df_relev1["Raridade"] = df_relev1["Raridade"].replace(raridade_nome)
df_relev2["Raridade"] = df_relev2["Raridade"].replace(raridade_nome)

df_relev2_unico = df_relev2.drop_duplicates(subset=["Id", "Shiny", "Raridade"])

df = df_relev1.merge(df_relev2_unico[["Id", "Shiny","Raridade", "Valor"]], on=["Id", "Shiny", "Raridade"], how="left")
df = df.drop(columns=["configData","category"])
df["Tamanho"] = "Normal"
df.loc[df["Id"].str.contains("Huge"), "Tamanho"] = "Huge"
df.loc[df["Id"].str.contains("Titanic"), "Tamanho"] = "Titanic"
df.loc[df["Id"].str.contains("Gargantuan"), "Tamanho"] = "Gargantuan"
colunas = list(df.columns)
indice_raridade = colunas.index("Raridade")
colunas.remove("Tamanho")
colunas.insert(indice_raridade, "Tamanho")
df = df[colunas]
df.to_csv('ps99_pet_data.csv')
files.download('ps99_pet_data.csv')
df

Mounted at /content/drive


<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

Existe                              Id     Tamanho Raridade  \
0           212,391,172                          Turtle      Normal   Normal   
1               819,211                  Unicorn Dragon      Normal   Normal   
2            39,153,161                   Scarecrow Cat      Normal   Golden   
3           235,951,033                         Ladybug      Normal   Normal   
4            67,441,304                           Llama      Normal   Normal   
5           334,789,411                           Piggy      Normal   Normal   
6            34,801,464                   Ugly Duckling      Normal   Golden   
7           272,456,805                   Ugly Duckling      Normal   Normal   
8            34,966,982                         Ladybug      Normal   Golden   
9             6,675,825                          Turtle      Normal  Rainbow   
10          300,088,617                   Scarecrow Cat      Normal   Normal   
11           85,931,375                        Hedgehog      Normal   Normal   
12                  282                  Titanic Banana     Titanic   Normal   
13       15,137,342,170                           Corgi      Normal   Normal   
14               21,458           Huge Pink Balloon Cat        Huge   Normal   
15       15,128,212,124                             Dog      Normal   Normal   
16       15,128,336,243                             Cat      Normal   Normal   
17       15,139,745,617                         Axolotl      Normal   Normal   
18           27,503,877                         Axolotl      Normal   Normal   
19          182,484,597                            Bear      Normal   Normal   
20        1,967,727,247                           Bunny      Normal   Normal   
21          866,782,356                     White Bunny      Normal   Normal   
22          428,854,832                        Squirrel      Normal   Normal   
23          443,707,994                      Mining Dog      Normal   Normal   
24          143,816,427                         Firefly      Normal   Normal   
25          525,875,894                         Chicken      Normal   Normal   
26           41,973,238                      Mining Dog      Normal   Golden   
27           18,921,941                      Happy Rock      Normal   Golden   
28           63,668,692                          Dragon      Normal   Normal   
29          186,453,358                      Happy Rock      Normal   Normal   
30          392,315,558                        Platypus      Normal   Normal   
31          135,684,399                     Green Cobra      Normal   Normal   
32            3,655,817                     Willow Wisp      Normal  Rainbow   
33          222,016,251                             Bat      Normal   Normal   
34           47,666,191                     Willow Wisp      Normal   Normal   
35                1,909          Huge White Balloon Cat        Huge   Normal   
36            3,586,999                           Agony      Normal  Rainbow   
37          238,846,094                         Cyclops      Normal   Normal   
38              101,400                         Pop Cat      Normal   Normal   
39                   82              Titanic Hippomelon     Titanic   Normal   
40          238,846,749                           Slime      Normal   Normal   
41           56,275,359                           Agony      Normal   Normal   
42          865,320,441                       Dalmatian      Normal   Normal   
43           25,355,420                  Shadow Griffin      Normal   Golden   
44              144,148                           Chick      Normal   Golden   
45           91,436,093                           Chick      Normal   Golden   
46          126,783,370                        Flamingo      Normal   Normal   
47          364,384,105                             Bee      Normal   Normal   
48              291,293                       Knife Cat      Normal   Normal   
49          915,7

In [ ]:
!pip uninstall -y pandas
!pip install pandas --upgrade --force-reinstall

Found existing installation: pandas 2.2.2
Uninstalling pandas-2.2.2:
  Successfully uninstalled pandas-2.2.2
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 89.9/89.9 kB 4.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 62.0/62.0 kB 4.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.1/13.1 MB 76.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 16.4/16.4 MB 66.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 229.9/229.9 kB 18.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 509.2/509.2 kB 32.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 347.8/347.8 kB 24.0 MB/s eta 0:00:00
  Attempting uninstall: pytz
    Found existing installation: pytz 2025.2
    Uninstalling pytz-2025.2:
      Successfully uninstalled pytz-2025.2
  Attempting uninstall: tzdata
    Found existing installation: tzdata 2025.2
    Uninstalling tzdata-2025.2:
      Successfully uninstalled tzdata-2025.2
  Attempting uninstall: six
